# Extracció d'entitats anomenades (Pràctica 3)

In [75]:
import nltk
nltk.download('conll2002')
from nltk.corpus import conll2002
from nltk.tag import CRFTagger
from nltk.stem import WordNetLemmatizer
nltk.download('averaged_perceptron_tagger')
nltk.download('wordnet')
from typing import List


[nltk_data] Downloading package conll2002 to
[nltk_data]     C:\Users\Usuario\AppData\Roaming\nltk_data...
[nltk_data]   Package conll2002 is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\Usuario\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Usuario\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


## Experimentació de get_features

A continuació, farem tres versions de la funció 'get_features'. Totes tres funcions prenen una llista de tokens i un índex com a entrada, i retornen la llista de característiques per al token en l'índex indicat. Aquestes característiques s'utilitzen després en l'entrenament i l'etiquetatge del model CRF utilitzat.

### Prefixos, lemmas, POS-Tags

Definim les funcions 'lemma' i 'pos_tag' per tal d'inicialitzar el lematitzador i l'etiquetador POS:

  La funció 'lemma(word)' utilitza el lematitzador WordNetLemmatizer de NLTK per obtenir el lema (forma base d'una paraula) de la paraula.
  
  La funció 'pos_tag(word)' utilitza nltk.pos_tag per obtenir l'etiqueta POS d'una paraula (si és un sustantiu, verb, etc.)

In [ ]:
# Inicialitza el lematitzador i l'etiquetador POS
lemmatizer = WordNetLemmatizer()

def lemma(word):
    """
    Obtiene el lema de una palabra utilizando WordNetLemmatizer de NLTK.
    """
    return lemmatizer.lemmatize(word)

def pos_tag(word):
    """
    Obtiene la etiqueta POS (Part-of-Speech) de una palabra utilizando
    nltk.pos_tag.
    """
    tagged = nltk.pos_tag([word])
    return tagged[0][1]

En aquesat primera versió de 'get_features' la llisat de característiques pel token és:

- La paraula actual.
- Si la paraula està en majúscules.
- Si la paraula te signes de puntuació.
- Si la paraula te números.
- El sufix de 3 caràcters.
- El prefix de 3 caràcters.
- El lema de la paraula.
- L'etiqueta POS de la paraula.

In [ ]:
def get_features1(tokens, idx):
    """
    Función original de extracción de características utilizada por defecto en nltk.tag.CRFTagger.

    :param tokens: Lista de tokens (palabras).
    :param idx: Índice del token actual en la lista de tokens.
    :return: Lista de características del token en el índice dado.
    """
    word = tokens[idx]

    # Característiques bàsiques
    features = [
        'word=' + word,                   # Paraula actual
        'is_upper=' + str(word.isupper()), # ¿És majúscula?
        'has_punct=' + str(any(char in word for char in '.,;:!?')),  # ¿Te signes de puntuaci?
        'has_numbers=' + str(any(char.isdigit() for char in word)),  # ¿Te números?
        'suffix=' + word[-3:],            # Sufix de 3 caràcters
        'prefix=' + word[:3],   # Prefix de 3 caràcters
        'lemma=' + lemmatizer.lemmatize(word),  # Lema de la paraula
        'pos_tag=' + pos_tag(word),  # Etiqueta POS
    ]

    return features


### Morfologia i longitud

En aquesta segona versió de 'get_features' les característiques inclouen:
- La paraula actual.
- Si la paraula està en majúscules.
- Si la paraula te signes de puntuació.
- Si la paraula te números.
- El sufix de 3 caràcters.
- El prefix de 3 caràcters.
- La longitud de la paraula.
- Les característiques de morfología obtingudes de la funció morfology_features.

Es defineix la funció morfology_features, que pren una paraula i retorna les característiques de morfología esecífiques. Hem afegit algunes característiques per quan el text és en espanyol, unes altres per quan és en neerlandès i finalment també hem afegit característiques per l'anglès, ja que en l'apartat opcional també s'utilitza aquesta funció i els texton estàn en anglès. 

Per quan és en espanyol:
- Si acaba en 'ando' o 'endo', s'agrega la característica 'ending_gerund'.
- Si la paraula acaba en 'ado' o 'ido', s'agrega la característica 'ending_past_participle'.
- Si acaba en 'mente', s'agrega la característica 'ending_adverb_ly'.

Per quan és en neerlandès:
- Si la paraula acaba en 'end' o 'ing', s'agrega la característica 'ending_gerund'.
- Si la paraula acaba en 'd' o 't', s'agrega la característica 'ending_past_participle'.

Per quan és en anglès:
- Si acaba en 'ing', s'agrega la característica 'ending_gerund'.
- Si la paraula acaba en 'ed', s'agrega la característica 'ending_past_participle'.
- Si acaba en 'ly', s'agrega la característica 'ending_adverb_ly'.


In [ ]:
def get_features2(tokens: List[str], idx: int) -> List[str]:
    word = tokens[idx]
    features = [
        'word=' + word,
        'is_upper=' + str(word.isupper()),
        'has_punct=' + str(any(char in word for char in '.,;:!?')),
        'has_numbers=' + str(any(char.isdigit() for char in word)),
        'suffix=' + word[-3:],  # sufix de 3 caràcters
        'prefix=' + word[:3],   # prefix de 3 caràcters
        'length=' + str(len(word)),  # Longitud de la paraula
        'morfology=' + morfology_features(word),  # Característiques de morfología
        
    ]
    return features

def morfology_features(word):
    """
    Obtiene características de morfología de una palabra.
    """
    morfology = ''
    #per espanyol
    if word.endswith('ando') or word.endswith('endo'):
        morfology += 'ending_gerund '
    if word.endswith('ado') or word.endswith('ido'):
        morfology += 'ending_past_participle '
    if word.endswith('mente'):
        morfology += 'ending_adverb_ly '

    #per neerlandès
    if word.endswith('end') or word.endswith('ing'):
        morfology += 'ending_gerund '
    if word.endswith('d') or word.endswith('t'):
        morfology += 'ending_past_participle '
    
    #per anglès
    if word.endswith('ing'):
        morfology += 'ending_gerund '
    if word.endswith('ed'):
        morfology += 'ending_past_participle '
    if word.endswith('ly'):
        morfology += 'ending_adverb_ly '

    return morfology.strip()

### Prefix, length, morfology, lemma, pos_tag

En aquesta versió hem combinat les dues versions anteriors. Per tant la llista de característiques inclou:

- La paraula actual.
- Si la paraula està en majúsculds.
- Si la paraula te signes de puntuació.
- Si la paraula te números.
- El sufix de 3 caràcters.
- El prefix de 3 caràcters.
- La longitud de la paraula.
- Las característiques de morfología obtingudes de la funció morfology_features.
- El lema de la paraula obtingut amb lemmatizer.
- L'etiqueta POS de la paraula obtinguda amb pos_tag.

In [ ]:
def get_features3(tokens: List[str], idx: int) -> List[str]:
    word = tokens[idx]
    features = [
        'word=' + word,
        'is_upper=' + str(word.isupper()),
        'has_punct=' + str(any(char in word for char in '.,;:!?')),
        'has_numbers=' + str(any(char.isdigit() for char in word)),
        'suffix=' + word[-3:],  # sufix de 3 caràcters
        'prefix=' + word[:3],   # prefix de 3 caràcters
        'length=' + str(len(word)),  # Longitud de la paraula
        'morfology=' + morfology_features(word),  # Característiques de morfología
        'lemma=' + lemmatizer.lemmatize(word),  # Lema de la paraula
        'pos_tag=' + pos_tag(word),  # Etiqueta POS
    ]
    return features

# Experiments amb diferents codificacions BIO, IO, BIOES

### Funcions per avaluar els models

La funció extract_real_entities s'utilitza per extreure les entitats reals a partir d'un "llistat" de paraules amb les seves etiquetes BIO, IO o BIOES. Això és necessari per poder avaluar correctament el rendiment del sistema i comparar les entitats reals amb les predites de manera precisa. És important assegurar-se que etiqueta bé tota l'entitat, ja que si etiqueta bé només una part de l'entitat no s'hauría de considerar correcte.

In [76]:
def extract_real_entities(sentences):
    entities = []
    for sentence in sentences:
        entity = []
        for word, tag in sentence:
            if tag != 'O':
                if entity and tag[0] != 'I':
                    entities.append(tuple(entity))
                    entity = [(word, tag[0:])]
                elif entity:
                    entity.append((word, tag[0:]))
                else:
                    entity = [(word, tag[0:])]
            elif entity:
                entities.append(tuple(entity))
                entity = []
        if entity:
            entities.append(tuple(entity))
    return entities

La funció 'calculate_metrics' s'utilitza per avaluar el rendiment del model. Pren com entrada les entitats predites per el model i les entitats reals, calcula els true positive, la precisió, el recall i la puntuació F1 i retorna aquests valors com a sortida.

In [77]:
def calculate_metrics(predicted_entities, real_entities):
    true_positives = len(predicted_entities.intersection(real_entities))
    if len(predicted_entities) == 0:
        precision = 0
    else:
        precision = true_positives / len(predicted_entities)
    if len(real_entities) == 0:
        recall = 0
    else:
        recall = true_positives / len(real_entities)
    if precision + recall == 0:
        f1_score = 0
    else:
        f1_score = 2 * (precision * recall) / (precision + recall)
    return precision, recall, f1_score


## Experiments amb BIO

A continuació entrenem i avaluem dos models d'etiquetat d'entitats utilitzant la codificació BIO (principi de l'entitat, dins de l'entitat, fora de l'entitat). Un model en espanyol i un en neerlandès.

### Model en espanyol

Primer carreguem el conjunt de dades per espanyol (train_esp, dev_esp i test_esp) del corpus CoNLL2002. Aquests conjunts de dades estàn en format (paraula, POS, etiqueta de l'entitat 'BIO')

In [371]:
train_esp = conll2002.iob_sents('esp.train')
dev_esp = conll2002.iob_sents('esp.testa')
test_esp = conll2002.iob_sents('esp.testb')

Eliminem les etiquetes POS, deixant nomès la paraula i l'etiqueta de l'entitat, ja que el que volem és predir l'etiqueta de l'entitat i el POS no ens interesa en aquest cas.

In [372]:
train_esp = [[(word, BIO) for word, _, BIO in sent] for sent in train_esp]
dev_esp = [[(word, BIO) for word, _, BIO in sent] for sent in dev_esp]
test_esp = [[(word, BIO) for word, _, BIO in sent] for sent in test_esp]

train_esp #per comprovar que esta ben fet

[[('Melbourne', 'B-LOC'),
  ('(', 'O'),
  ('Australia', 'B-LOC'),
  (')', 'O'),
  (',', 'O'),
  ('25', 'O'),
  ('may', 'O'),
  ('(', 'O'),
  ('EFE', 'B-ORG'),
  (')', 'O'),
  ('.', 'O')],
 [('-', 'O')],
 [('El', 'O'),
  ('Abogado', 'B-PER'),
  ('General', 'I-PER'),
  ('del', 'I-PER'),
  ('Estado', 'I-PER'),
  (',', 'O'),
  ('Daryl', 'B-PER'),
  ('Williams', 'I-PER'),
  (',', 'O'),
  ('subrayó', 'O'),
  ('hoy', 'O'),
  ('la', 'O'),
  ('necesidad', 'O'),
  ('de', 'O'),
  ('tomar', 'O'),
  ('medidas', 'O'),
  ('para', 'O'),
  ('proteger', 'O'),
  ('al', 'O'),
  ('sistema', 'O'),
  ('judicial', 'O'),
  ('australiano', 'O'),
  ('frente', 'O'),
  ('a', 'O'),
  ('una', 'O'),
  ('página', 'O'),
  ('de', 'O'),
  ('internet', 'O'),
  ('que', 'O'),
  ('imposibilita', 'O'),
  ('el', 'O'),
  ('cumplimiento', 'O'),
  ('de', 'O'),
  ('los', 'O'),
  ('principios', 'O'),
  ('básicos', 'O'),
  ('de', 'O'),
  ('la', 'O'),
  ('Ley', 'B-MISC'),
  ('.', 'O')],
 [('La', 'O'),
  ('petición', 'O'),
  ('del', '

Creem una instància de CRFTagger (Conditional Random Fields Tagger) i entrenem el model CRF amb les dades d'entrenament.

  Per realitzar les diferents proves amb característiques addicionals, s'ha de canviar el parametre que se li passa a CRFTagger(). Si volem fer la prova sense característiques addicionals, no afegim res. En cas de voler provar afegint features, passem com a paràmetre feature_func=get_features1, get_features2, o get_features3, depenent de quines volem provar

In [373]:
crf_tagger_esp = CRFTagger(feature_func=get_features) #canviar per get_features1, get_features2, get_features3 o res depenent de quin volem provar
crf_tagger_esp.train(train_esp, 'model_crf_esp.crf.tagger')

S'etiqueten les oracions del conjunt dev utilitzant el model entrenat anteriorment.

In [374]:
etiquetadas_dev_esp = crf_tagger_esp.tag_sents([word for word, _ in sent] for sent in dev_esp)
etiquetadas_dev_esp # Per comprovar si ho fa correctament

[[('Sao', 'B-LOC'),
  ('Paulo', 'I-LOC'),
  ('(', 'O'),
  ('Brasil', 'B-LOC'),
  (')', 'O'),
  (',', 'O'),
  ('23', 'O'),
  ('may', 'O'),
  ('(', 'O'),
  ('EFECOM', 'B-ORG'),
  (')', 'O'),
  ('.', 'O')],
 [('-', 'O')],
 [('La', 'O'),
  ('multinacional', 'O'),
  ('española', 'O'),
  ('Telefónica', 'B-ORG'),
  ('ha', 'O'),
  ('impuesto', 'O'),
  ('un', 'O'),
  ('récord', 'O'),
  ('mundial', 'O'),
  ('al', 'O'),
  ('poner', 'O'),
  ('en', 'O'),
  ('servicio', 'O'),
  ('tres', 'O'),
  ('millones', 'O'),
  ('de', 'O'),
  ('nuevas', 'O'),
  ('líneas', 'O'),
  ('en', 'O'),
  ('el', 'O'),
  ('estado', 'O'),
  ('brasileño', 'O'),
  ('de', 'O'),
  ('Sao', 'B-LOC'),
  ('Paulo', 'I-LOC'),
  ('desde', 'O'),
  ('que', 'O'),
  ('asumió', 'O'),
  ('el', 'O'),
  ('control', 'O'),
  ('de', 'O'),
  ('la', 'O'),
  ('operadora', 'O'),
  ('Telesp', 'B-ORG'),
  ('hace', 'O'),
  ('20', 'O'),
  ('meses', 'O'),
  (',', 'O'),
  ('anunció', 'O'),
  ('hoy', 'O'),
  ('el', 'O'),
  ('presidente', 'O'),
  ('de', 'O')

S'utilitza la funció extract_real_entities per extreure les entitats tant del conjunt dev_esp original com pel conjunt predit etiquetadas_dev_esp.

In [375]:
real_entities = extract_real_entities(dev_esp)
predicted_entities = extract_real_entities(etiquetadas_dev_esp)

Es calculen les métriques de precisió, recall i F1-score utilitzant la funció calculate_metrics i imprimim els resultats.

In [376]:
precision, recall, f1_score = calculate_metrics(set(predicted_entities), set(real_entities))
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1_score)

Precision: 0.7067221891731112
Recall: 0.5382872677843226
F1-score: 0.6111111111111112


### Model en neerlandès

Per tal d'entrenar i avaluar el model en neerandès seguim el mateix procediment que en el model anterior en castellà.

In [365]:
train_ned = conll2002.iob_sents('ned.train')
dev_ned = conll2002.iob_sents('ned.testa')
test_ned = conll2002.iob_sents('ned.testb')

In [366]:
train_ned = [[(word, BIO) for word, _, BIO in sent] for sent in train_ned]
dev_ned = [[(word, BIO) for word, _, BIO in sent] for sent in dev_ned]
test_ned = [[(word, BIO) for word, _, BIO in sent] for sent in test_ned]

In [367]:
crf_tagger_ned = CRFTagger(feature_func=get_features) #canviar per get_features1, get_features2, get_features3 o res depenent de quin volem provar
crf_tagger_ned.train(train_ned, 'model_crf_ned.crf.tagger')

In [368]:
etiquetadas_dev_ned = crf_tagger_ned.tag_sents([word for word, _ in sent] for sent in dev_ned)
etiquetadas_dev_ned

[[('Dat', 'O'),
  ('is', 'O'),
  ('verder', 'O'),
  ('opgelaaid', 'O'),
  ('door', 'O'),
  ('windsnelheden', 'O'),
  ('die', 'O'),
  ('oplopen', 'O'),
  ('tot', 'O'),
  ('35', 'O'),
  ('kilometer', 'O'),
  ('per', 'O'),
  ('uur', 'O'),
  ('.', 'O')],
 [('Bomaanslag', 'O'),
  ('op', 'O'),
  ('Indiase', 'B-MISC'),
  ('trein', 'O'),
  (':', 'O'),
  ('twaalf', 'O'),
  ('doden', 'O')],
 [('Ook', 'O'),
  ('in', 'O'),
  ('Californië', 'B-LOC'),
  (',', 'O'),
  ('in', 'O'),
  ('Sierra', 'B-PER'),
  ('Nevada', 'I-PER'),
  (',', 'O'),
  ('woeden', 'O'),
  ('al', 'O'),
  ('een', 'O'),
  ('week', 'O'),
  ('lang', 'O'),
  ('hevige', 'O'),
  ('bosbranden', 'O'),
  ('.', 'O')],
 [('De', 'O'),
  ('brand', 'O'),
  ('heeft', 'O'),
  ('vooral', 'O'),
  ('het', 'O'),
  ('nationale', 'O'),
  ('park', 'O'),
  ('van', 'O'),
  ('de', 'O'),
  ('Sequoia-indianen', 'O'),
  ('getroffen', 'O'),
  ('.', 'O')],
 [('De', 'O'),
  ('gestrande', 'O'),
  ('Concorde', 'O'),
  ('wordt', 'O'),
  ('nu', 'O'),
  ('aan', 'O'),

In [369]:
real_entities = extract_real_entities(dev_ned)
predicted_entities = extract_real_entities(etiquetadas_dev_ned)

In [370]:
precision, recall, f1_score = calculate_metrics(set(predicted_entities), set(real_entities))
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1_score)

Precision: 0.6951219512195121
Recall: 0.4481132075471698
F1-score: 0.5449330783938814


## Experiment amb IO

A continuació, provarem com funcionaria el model utilitzant la codificació IO en lloc de BIO, per veure si hi hauria millora o no. En aquest cas també crearem un model en espanyol i un en neerlandès seguint el mateix procediment que en els models anteriors.

### Model en espanyol

In [358]:
train_esp = conll2002.iob_sents('esp.train')
dev_esp = conll2002.iob_sents('esp.testa')
test_esp = conll2002.iob_sents('esp.testb')

In [359]:
#no agafem el tag
train_esp = [[(word, BIO) for word, _, BIO in sent] for sent in train_esp]
dev_esp = [[(word, BIO) for word, _, BIO in sent] for sent in dev_esp]
test_esp = [[(word, BIO) for word, _, BIO in sent] for sent in test_esp]

En aquest cas, com que el corpus conll2002 utilitza l'etiqueta de l'entitat en format BIO, hem de fer un canvi manual a format IO. Per fer-ho, canviem les B (begin) a I (inside), ja que si una paraula és el principi de l'entitat, significa que està dins de la entitat i, per tant, en format IO seria una etiqueta I.

In [360]:
train_esp = [[(word, 'I-' + bio[2:]) if bio.startswith('B-') else (word, bio) for word, bio in sent] for sent in train_esp]
dev_esp = [[(word, 'I-' + bio[2:]) if bio.startswith('B-') else (word, bio) for word, bio in sent] for sent in dev_esp]
test_esp = [[(word, 'I-' + bio[2:]) if bio.startswith('B-') else (word, bio) for word, bio in sent] for sent in test_esp]

train_esp # comprovem que s'hagi fet el canvi correctament

[[('Melbourne', 'I-LOC'),
  ('(', 'O'),
  ('Australia', 'I-LOC'),
  (')', 'O'),
  (',', 'O'),
  ('25', 'O'),
  ('may', 'O'),
  ('(', 'O'),
  ('EFE', 'I-ORG'),
  (')', 'O'),
  ('.', 'O')],
 [('-', 'O')],
 [('El', 'O'),
  ('Abogado', 'I-PER'),
  ('General', 'I-PER'),
  ('del', 'I-PER'),
  ('Estado', 'I-PER'),
  (',', 'O'),
  ('Daryl', 'I-PER'),
  ('Williams', 'I-PER'),
  (',', 'O'),
  ('subrayó', 'O'),
  ('hoy', 'O'),
  ('la', 'O'),
  ('necesidad', 'O'),
  ('de', 'O'),
  ('tomar', 'O'),
  ('medidas', 'O'),
  ('para', 'O'),
  ('proteger', 'O'),
  ('al', 'O'),
  ('sistema', 'O'),
  ('judicial', 'O'),
  ('australiano', 'O'),
  ('frente', 'O'),
  ('a', 'O'),
  ('una', 'O'),
  ('página', 'O'),
  ('de', 'O'),
  ('internet', 'O'),
  ('que', 'O'),
  ('imposibilita', 'O'),
  ('el', 'O'),
  ('cumplimiento', 'O'),
  ('de', 'O'),
  ('los', 'O'),
  ('principios', 'O'),
  ('básicos', 'O'),
  ('de', 'O'),
  ('la', 'O'),
  ('Ley', 'I-MISC'),
  ('.', 'O')],
 [('La', 'O'),
  ('petición', 'O'),
  ('del', '

In [361]:
crf_tagger_esp = CRFTagger(feature_func=get_features) #canviar per get_features1, get_features2, get_features3 o res depenent de quin volem provar

crf_tagger_esp.train(train_esp, 'model_crf_esp.crf.tagger')

In [362]:
etiquetadas_dev_esp = crf_tagger_esp.tag_sents([word for word, _ in sent] for sent in dev_esp)

etiquetadas_dev_esp

[[('Sao', 'I-LOC'),
  ('Paulo', 'I-LOC'),
  ('(', 'O'),
  ('Brasil', 'I-LOC'),
  (')', 'O'),
  (',', 'O'),
  ('23', 'O'),
  ('may', 'O'),
  ('(', 'O'),
  ('EFECOM', 'I-ORG'),
  (')', 'O'),
  ('.', 'O')],
 [('-', 'O')],
 [('La', 'O'),
  ('multinacional', 'O'),
  ('española', 'O'),
  ('Telefónica', 'I-ORG'),
  ('ha', 'O'),
  ('impuesto', 'O'),
  ('un', 'O'),
  ('récord', 'O'),
  ('mundial', 'O'),
  ('al', 'O'),
  ('poner', 'O'),
  ('en', 'O'),
  ('servicio', 'O'),
  ('tres', 'O'),
  ('millones', 'O'),
  ('de', 'O'),
  ('nuevas', 'O'),
  ('líneas', 'O'),
  ('en', 'O'),
  ('el', 'O'),
  ('estado', 'O'),
  ('brasileño', 'O'),
  ('de', 'O'),
  ('Sao', 'I-LOC'),
  ('Paulo', 'I-LOC'),
  ('desde', 'O'),
  ('que', 'O'),
  ('asumió', 'O'),
  ('el', 'O'),
  ('control', 'O'),
  ('de', 'O'),
  ('la', 'O'),
  ('operadora', 'O'),
  ('Telesp', 'I-ORG'),
  ('hace', 'O'),
  ('20', 'O'),
  ('meses', 'O'),
  (',', 'O'),
  ('anunció', 'O'),
  ('hoy', 'O'),
  ('el', 'O'),
  ('presidente', 'O'),
  ('de', 'O')

In [363]:
real_entities = extract_real_entities(dev_esp)
predicted_entities = extract_real_entities(etiquetadas_dev_esp)

In [ ]:
real_entities #per comprovar que es facin les entitats correctament

In [ ]:
predicted_entities #per comprovar que es facin les entitats correctament

In [364]:
precision, recall, f1_score = calculate_metrics(set(predicted_entities), set(real_entities))
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1_score)

Precision: 0.6732307692307692
Recall: 0.49637023593466423
F1-score: 0.5714285714285714


### Model en neerlandès

Fem el mateix procediment que en el model en espanyol, carreguem les dades, convertim a format IO, Entrenem el model i l'avaluem.

In [351]:
train_ned = conll2002.iob_sents('ned.train')
dev_ned = conll2002.iob_sents('ned.testa')
test_ned = conll2002.iob_sents('ned.testb')

In [352]:
train_ned = [[(word, BIO) for word, _, BIO in sent] for sent in train_ned]
dev_ned = [[(word, BIO) for word, _, BIO in sent] for sent in dev_ned]
test_ned = [[(word, BIO) for word, _, BIO in sent] for sent in test_ned]

In [353]:
train_ned = [[(word, 'I-' + bio[2:]) if bio.startswith('B-') else (word, bio) for word, bio in sent] for sent in train_ned]
dev_ned = [[(word, 'I-' + bio[2:]) if bio.startswith('B-') else (word, bio) for word, bio in sent] for sent in dev_ned]
test_ned = [[(word, 'I-' + bio[2:]) if bio.startswith('B-') else (word, bio) for word, bio in sent] for sent in test_ned]

In [354]:
crf_tagger_ned = CRFTagger(feature_func=get_features)  #canviar per get_features1, get_features2, get_features3 o res depenent de quin volem provar
crf_tagger_ned.train(train_ned, 'model_crf_ned.crf.tagger')

In [355]:
etiquetadas_dev_ned = crf_tagger_ned.tag_sents([word for word, _ in sent] for sent in dev_ned)
etiquetadas_dev_ned

[[('Dat', 'O'),
  ('is', 'O'),
  ('verder', 'O'),
  ('opgelaaid', 'O'),
  ('door', 'O'),
  ('windsnelheden', 'O'),
  ('die', 'O'),
  ('oplopen', 'O'),
  ('tot', 'O'),
  ('35', 'O'),
  ('kilometer', 'O'),
  ('per', 'O'),
  ('uur', 'O'),
  ('.', 'O')],
 [('Bomaanslag', 'O'),
  ('op', 'O'),
  ('Indiase', 'I-MISC'),
  ('trein', 'O'),
  (':', 'O'),
  ('twaalf', 'O'),
  ('doden', 'O')],
 [('Ook', 'O'),
  ('in', 'O'),
  ('Californië', 'I-LOC'),
  (',', 'O'),
  ('in', 'O'),
  ('Sierra', 'I-PER'),
  ('Nevada', 'I-PER'),
  (',', 'O'),
  ('woeden', 'O'),
  ('al', 'O'),
  ('een', 'O'),
  ('week', 'O'),
  ('lang', 'O'),
  ('hevige', 'O'),
  ('bosbranden', 'O'),
  ('.', 'O')],
 [('De', 'O'),
  ('brand', 'O'),
  ('heeft', 'O'),
  ('vooral', 'O'),
  ('het', 'O'),
  ('nationale', 'O'),
  ('park', 'O'),
  ('van', 'O'),
  ('de', 'O'),
  ('Sequoia-indianen', 'O'),
  ('getroffen', 'O'),
  ('.', 'O')],
 [('De', 'O'),
  ('gestrande', 'O'),
  ('Concorde', 'O'),
  ('wordt', 'O'),
  ('nu', 'O'),
  ('aan', 'O'),

In [356]:
real_entities = extract_real_entities(dev_ned)
predicted_entities = extract_real_entities(etiquetadas_dev_ned)

In [357]:
precision, recall, f1_score = calculate_metrics(set(predicted_entities), set(real_entities))
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1_score)

Precision: 0.6353919239904988
Recall: 0.4276578737010392
F1-score: 0.5112279025322504


## Experiment amb BIOES

També hem volgut experimentar amb la codificació BIOES. Primer, definim la funció 'convert_bio_to_bioes'. Aquesta funció s'encarrega de convertir les etiquetes de format BIO a format BIOES (Begin, Inside, Outside, End, Single). Si l'etiqeuta en BIO és 'O', es manté igual. Si és 'B', es converteix a 'S' si la següent paraula no és 'I' (indicant que és una entitat d'una única paraula). Si és 'I', es converteix a 'E' si la següent paraula no és 'I' (indicant que és el final de l'entitat).

In [322]:
def convert_bio_to_bioes(bio_tags):
    bioes_tags = []
    for i, (word, tag) in enumerate(bio_tags):
        if tag == 'O':
            bioes_tags.append((word, tag))
        elif tag.startswith('B-'):
            if i + 1 < len(bio_tags) and bio_tags[i + 1][1].startswith('I-'):
                bioes_tags.append((word, tag))
            else:
                bioes_tags.append((word, tag.replace('B-', 'S-')))
        elif tag.startswith('I-'):
            if i + 1 < len(bio_tags) and bio_tags[i + 1][1].startswith('I-'):
                bioes_tags.append((word, tag))
            else:
                bioes_tags.append((word, tag.replace('I-', 'E-')))
    return bioes_tags

### Model en espanyol

In [204]:
train_esp = conll2002.iob_sents('esp.train')
dev_esp = conll2002.iob_sents('esp.testa')
test_esp = conll2002.iob_sents('esp.testb')

In [205]:
train_esp = [[(word, BIO) for word, _, BIO in sent] for sent in train_esp]
dev_esp = [[(word, BIO) for word, _, BIO in sent] for sent in dev_esp]
test_esp = [[(word, BIO) for word, _, BIO in sent] for sent in test_esp]

In [206]:
# Convertim les dades a BIOES
train_esp = [convert_bio_to_bioes(sent) for sent in train_esp]
dev_esp = [convert_bio_to_bioes(sent) for sent in dev_esp]
test_esp = [convert_bio_to_bioes(sent) for sent in test_esp]

In [120]:
train_esp # per comporvar que està be

[[('Melbourne', 'S-LOC'),
  ('(', 'O'),
  ('Australia', 'S-LOC'),
  (')', 'O'),
  (',', 'O'),
  ('25', 'O'),
  ('may', 'O'),
  ('(', 'O'),
  ('EFE', 'S-ORG'),
  (')', 'O'),
  ('.', 'O')],
 [('-', 'O')],
 [('El', 'O'),
  ('Abogado', 'B-PER'),
  ('General', 'I-PER'),
  ('del', 'I-PER'),
  ('Estado', 'E-PER'),
  (',', 'O'),
  ('Daryl', 'B-PER'),
  ('Williams', 'E-PER'),
  (',', 'O'),
  ('subrayó', 'O'),
  ('hoy', 'O'),
  ('la', 'O'),
  ('necesidad', 'O'),
  ('de', 'O'),
  ('tomar', 'O'),
  ('medidas', 'O'),
  ('para', 'O'),
  ('proteger', 'O'),
  ('al', 'O'),
  ('sistema', 'O'),
  ('judicial', 'O'),
  ('australiano', 'O'),
  ('frente', 'O'),
  ('a', 'O'),
  ('una', 'O'),
  ('página', 'O'),
  ('de', 'O'),
  ('internet', 'O'),
  ('que', 'O'),
  ('imposibilita', 'O'),
  ('el', 'O'),
  ('cumplimiento', 'O'),
  ('de', 'O'),
  ('los', 'O'),
  ('principios', 'O'),
  ('básicos', 'O'),
  ('de', 'O'),
  ('la', 'O'),
  ('Ley', 'S-MISC'),
  ('.', 'O')],
 [('La', 'O'),
  ('petición', 'O'),
  ('del', '

In [347]:
crf_tagger_esp = CRFTagger(feature_func=get_features) #canviar per get_features1, get_features2, get_features3 o res depenent de quin volem provar
crf_tagger_esp.train(train_esp, 'model_crf_esp_bioes.crf.tagger')

In [348]:
etiquetadas_dev_esp = crf_tagger_esp.tag_sents([[word for word, _ in sent] for sent in dev_esp])

In [349]:
real_entities = extract_real_entities(dev_esp)
predicted_entities = extract_real_entities(etiquetadas_dev_esp)

In [350]:
precision, recall, f1_score = calculate_metrics(set(predicted_entities), set(real_entities))
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1_score)

Precision: 0.7452440033085195
Recall: 0.6044951358604496
F1-score: 0.6675310242637525


### Model en neerlandès

In [337]:
train_ned = conll2002.iob_sents('ned.train')
dev_ned = conll2002.iob_sents('ned.testa')
test_ned = conll2002.iob_sents('ned.testb')

In [338]:
train_ned = [[(word, BIO) for word, _, BIO in sent] for sent in train_ned]
dev_ned = [[(word, BIO) for word, _, BIO in sent] for sent in dev_ned]
test_ned = [[(word, BIO) for word, _, BIO in sent] for sent in test_ned]

In [339]:
# Convertim les dades a BIOES
train_ned = [convert_bio_to_bioes(sent) for sent in train_ned]
dev_ned = [convert_bio_to_bioes(sent) for sent in dev_ned]
test_ned = [convert_bio_to_bioes(sent) for sent in test_ned]

In [340]:
crf_tagger_ned = CRFTagger(feature_func=get_features) #canviar per get_features1, get_features2, get_features3 o res depenent de quin volem provar

crf_tagger_ned.train(train_ned, 'model_crf_ned.crf.tagger')

In [341]:
etiquetadas_dev_ned = crf_tagger_ned.tag_sents([word for word, _ in sent] for sent in dev_ned)

In [63]:
etiquetadas_dev_ned

[[('Dat', 'O'),
  ('is', 'O'),
  ('verder', 'O'),
  ('opgelaaid', 'O'),
  ('door', 'O'),
  ('windsnelheden', 'O'),
  ('die', 'O'),
  ('oplopen', 'O'),
  ('tot', 'O'),
  ('35', 'O'),
  ('kilometer', 'O'),
  ('per', 'O'),
  ('uur', 'O'),
  ('.', 'O')],
 [('Bomaanslag', 'O'),
  ('op', 'O'),
  ('Indiase', 'S-MISC'),
  ('trein', 'O'),
  (':', 'O'),
  ('twaalf', 'O'),
  ('doden', 'O')],
 [('Ook', 'O'),
  ('in', 'O'),
  ('Californië', 'S-LOC'),
  (',', 'O'),
  ('in', 'O'),
  ('Sierra', 'B-PER'),
  ('Nevada', 'E-PER'),
  (',', 'O'),
  ('woeden', 'O'),
  ('al', 'O'),
  ('een', 'O'),
  ('week', 'O'),
  ('lang', 'O'),
  ('hevige', 'O'),
  ('bosbranden', 'O'),
  ('.', 'O')],
 [('De', 'O'),
  ('brand', 'O'),
  ('heeft', 'O'),
  ('vooral', 'O'),
  ('het', 'O'),
  ('nationale', 'O'),
  ('park', 'O'),
  ('van', 'O'),
  ('de', 'O'),
  ('Sequoia-indianen', 'S-MISC'),
  ('getroffen', 'O'),
  ('.', 'O')],
 [('De', 'O'),
  ('gestrande', 'O'),
  ('Concorde', 'O'),
  ('wordt', 'O'),
  ('nu', 'O'),
  ('aan', 

In [342]:
real_entities = extract_real_entities(dev_ned)
predicted_entities = extract_real_entities(etiquetadas_dev_ned)

In [343]:
precision, recall, f1_score = calculate_metrics(set(predicted_entities), set(real_entities))
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1_score)

Precision: 0.7584014532243415
Recall: 0.4979129397734049
F1-score: 0.6011519078473722


# Selecció del millor model i avaluació final

Una vegada seleccionat el model amb el millor rendiment utilitzant el conjunt de dades desenvolupament (dev), avaluem el seu rendiment amb el conjunt de proves. D'aquesta manera, podrem confirmar la seva eficàcia i generalitzabilitat.

Primer avaluem el model en espanyol. El model guanyador ha sigut el que utilitza l'etiquetatge de les entitats BIOES, i la tercera verció del get_features amb les següents característiques:
- La paraula actual.
- Si la paraula està en majúsculds.
- Si la paraula te signes de puntuació.
- Si la paraula te números.
- El sufix de 3 caràcters.
- El prefix de 3 caràcters.
- La longitud de la paraula.
- Las característiques de morfología obtingudes de la funció morfology_features.
- El lema de la paraula obtingut amb lemmatizer.
- L'etiqueta POS de la paraula obtinguda amb pos_tag.

In [233]:
train_esp = conll2002.iob_sents('esp.train')
dev_esp = conll2002.iob_sents('esp.testa')
test_esp = conll2002.iob_sents('esp.testb')

In [234]:
train_esp = [[(word, BIO) for word, _, BIO in sent] for sent in train_esp]
dev_esp = [[(word, BIO) for word, _, BIO in sent] for sent in dev_esp]
test_esp = [[(word, BIO) for word, _, BIO in sent] for sent in test_esp]

In [235]:
# Convertim les dades a BIOES
train_esp = [convert_bio_to_bioes(sent) for sent in train_esp]
dev_esp = [convert_bio_to_bioes(sent) for sent in dev_esp]
test_esp = [convert_bio_to_bioes(sent) for sent in test_esp]

In [236]:
crf_tagger_esp = CRFTagger(feature_func=get_features3) 
crf_tagger_esp.train(train_esp, 'model_crf_esp_bioes.crf.tagger')

In [381]:
etiquetadas_test_esp = crf_tagger_esp.tag_sents([[word for word, _ in sent] for sent in test_esp])

In [383]:
real_entities = extract_real_entities(test_esp)
predicted_entities = extract_real_entities(etiquetadas_test_esp)

In [384]:
precision, recall, f1_score = calculate_metrics(set(predicted_entities), set(real_entities))
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1_score)

Precision: 0.7799597180261832
Recall: 0.6261115602263541
F1-score: 0.6946188340807175


El model guanyador en neerlandès és el mateix que en espanyol, BIOES i la versió get_features3

In [237]:
train_ned = conll2002.iob_sents('ned.train')
dev_ned = conll2002.iob_sents('ned.testa')
test_ned = conll2002.iob_sents('ned.testb')

In [238]:
train_ned = [[(word, BIO) for word, _, BIO in sent] for sent in train_ned]
dev_ned = [[(word, BIO) for word, _, BIO in sent] for sent in dev_ned]
test_ned = [[(word, BIO) for word, _, BIO in sent] for sent in test_ned]

In [239]:
# Convertim les dades a BIOES
train_ned = [convert_bio_to_bioes(sent) for sent in train_ned]
dev_ned = [convert_bio_to_bioes(sent) for sent in dev_ned]
test_ned = [convert_bio_to_bioes(sent) for sent in test_ned]

In [240]:
crf_tagger_ned = CRFTagger(feature_func=get_features3) 

crf_tagger_ned.train(train_ned, 'model_crf_ned.crf.tagger')

In [389]:
etiquetadas_test_ned = crf_tagger_ned.tag_sents([word for word, _ in sent] for sent in test_ned)

In [390]:
real_entities = extract_real_entities(test_ned)
predicted_entities = extract_real_entities(etiquetadas_test_ned)

In [391]:
precision, recall, f1_score = calculate_metrics(set(predicted_entities), set(real_entities))
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1_score)

Precision: 0.7626412849494348
Recall: 0.5107569721115538
F1-score: 0.6117871629682653


## Prova amb textos reals

Per avaluar el nostre model també hem utilitzat textos reals, tenim 20 frases en espanyol i 20 en neerlandès amb el format que ens interessa per tal d'avaluar el model.

In [247]:
text_esp = [[('Barcelona', 'B-LOC'), ('es', 'O'), ('una', 'O'), ('ciudad', 'O'), ('maravillosa', 'O')], 
            [('Juan', 'B-PER'), ('Pérez', 'I-PER'), ('trabaja', 'O'), ('en', 'O'), ('Microsoft', 'B-ORG')],
            [('El', 'O'), ('Río', 'B-LOC'), ('Amazonas', 'I-LOC'), ('es', 'O'), ('impresionante', 'O')],
            [('La', 'O'), ('ONU', 'B-ORG'), ('tiene', 'O'), ('sede', 'O'), ('en', 'O'), ('Nueva', 'B-LOC'), ('York', 'I-LOC')],
            [('Santiago', 'B-PER'), ('viaja', 'O'), ('a', 'O'), ('Madrid', 'B-LOC'), ('este', 'O'), ('verano', 'O')],
            [('Apple', 'B-ORG'), ('inaugurará', 'O'), ('una', 'O'), ('tienda', 'O'), ('en', 'O'), ('Berlín', 'B-LOC')],
            [('Carmen', 'B-PER'), ('compró', 'O'), ('boletos', 'O'), ('para', 'O'), ('el', 'O'), ('Museo', 'B-ORG'), ('del', 'I-ORG'), ('Prado', 'I-ORG')],
            [('Los', 'O'), ('Alpes', 'B-LOC'), ('son', 'O'), ('popular', 'O'), ('destino', 'O'), ('turístico', 'O')],
            [('La', 'O'), ('FIFA', 'B-ORG'), ('organiza', 'O'), ('el', 'O'), ('Mundial', 'O')],
            [('Teresa', 'B-PER'), ('y', 'O'), ('José', 'B-PER'), ('visitarán', 'O'), ('la', 'O'), ('Torre', 'B-LOC'), ('Eiffel', 'I-LOC')],
            [('Madrid', 'B-LOC'), ('es', 'O'), ('la', 'O'), ('capital', 'O'), ('de', 'O'), ('España', 'B-LOC')],
            [('Pablo', 'B-PER'), ('Picasso', 'I-PER'), ('fue', 'O'), ('un', 'O'), ('pintor', 'O'), ('muy', 'O'), ('influyente', 'O')],
            [('El', 'O'), ('Támesis', 'B-LOC'), ('atraviesa', 'O'), ('Londres', 'B-LOC')],
            [('El', 'O'), ('Real', 'B-ORG'), ('Madrid', 'I-ORG'), ('ganó', 'O'), ('la', 'O'), ('Champions', 'O'), ('League', 'O')],
            [('Gaudí', 'B-PER'), ('diseñó', 'O'), ('la', 'O'), ('Sagrada', 'B-LOC'), ('Familia', 'I-LOC')],
            [('El', 'O'), ('Carnaval', 'O'), ('de', 'O'), ('Río', 'B-LOC'), ('de', 'I-LOC'), ('Janeiro', 'I-LOC'), ('es', 'O'), ('muy', 'O'), ('popular', 'O')],
            [('Los', 'O'), ('Pyrenees', 'B-LOC'), ('son', 'O'), ('una', 'O'), ('cadena', 'O'), ('montañosa', 'O')],
            [('Frida', 'B-PER'), ('Kahlo', 'I-PER'), ('fue', 'O'), ('una', 'O'), ('pintora', 'O'), ('mexicana', 'O')],
            [('La', 'O'), ('NASA', 'B-ORG'), ('envía', 'O'), ('misiones', 'O'), ('espaciales', 'O')],
            [('El', 'O'), ('Atlántico', 'B-LOC'), ('baña', 'O'), ('las', 'O'), ('costas', 'O'), ('de', 'O'), ('España', 'B-LOC')]
            ]

text_ned = [[('Amsterdam', 'B-LOC'), ('is', 'O'), ('de', 'O'), ('hoofdstad', 'O'), ('van', 'O'), ('Nederland', 'B-LOC')],
            [('KLM', 'B-ORG'), ('is', 'O'), ('gebaseerd', 'O'), ('in', 'O'), ('Amsterdam', 'B-LOC')],
            [('De', 'O'), ('Rijn', 'B-LOC'), ('stroomt', 'O'), ('door', 'O'), ('Duitsland', 'B-LOC')],
            [('Johannes', 'B-PER'), ('Vermeer', 'I-PER'), ('was', 'O'), ('een', 'O'), ('beroemde', 'O'), ('schilder', 'O')],
            [('Het', 'O'), ('Rode', 'B-ORG'), ('Kruis', 'I-ORG'), ('helpt', 'O'), ('mensen', 'O'), ('wereldwijd', 'O')],
            [('De', 'O'), ('Universiteit', 'B-ORG'), ('van', 'I-ORG'), ('Amsterdam', 'I-ORG'), ('is', 'O'), ('oud', 'O')],
            [('Rotterdam', 'B-LOC'), ('is', 'O'), ('een', 'O'), ('belangrijke', 'O'), ('havenstad', 'O')],
            [('Albert', 'B-PER'), ('Einstein', 'I-PER'), ('was', 'O'), ('een', 'O'), ('natuurkundige', 'O')],
            [('De', 'O'), ('Europese', 'B-ORG'), ('Unie', 'I-ORG'), ('bevordert', 'O'), ('samenwerking', 'O'), ('tussen', 'O'), ('Europese', 'B-LOC'), ('landen', 'O')],
            [('De', 'O'), ('Tweede', 'B-ORG'), ('Kamer', 'I-ORG'), ('debateert', 'O'), ('over', 'O'), ('wetgeving', 'O')],
            [('Brussel', 'B-LOC'), ('is', 'O'), ('de', 'O'), ('hoofdstad', 'O'), ('van', 'O'), ('België', 'B-LOC')],
            [('Vincent', 'B-PER'), ('van', 'O'), ('Gogh', 'I-PER'), ('was', 'O'), ('een', 'O'), ('Nederlands', 'O'), ('schilder', 'O')],
            [('De', 'O'), ('Maas', 'B-LOC'), ('stroomt', 'O'), ('door', 'O'), ('Nederland', 'B-LOC')],
            [('Het', 'O'), ('Anne', 'B-LOC'), ('Frank', 'I-LOC'), ('Huis', 'I-LOC'), ('is', 'O'), ('een', 'O'), ('beroemde', 'O'), ('attractie', 'O')],
            [('De', 'O'), ('Nederlandse', 'B-LOC'), ('Regering', 'I-LOC'), ('zetelt', 'O'), ('in', 'O'), ('Den', 'B-LOC'), ('Haag', 'I-LOC')],
            [('Rembrandt', 'B-PER'), ('was', 'O'), ('een', 'O'), ('vooraanstaande', 'O'), ('schilder', 'O'), ('in', 'O'), ('de', 'O'), ('Gouden', 'O'), ('Eeuw', 'O')],
            [('De', 'O'), ('Noordzee', 'B-LOC'), ('ligt', 'O'), ('aan', 'O'), ('de', 'O'), ('kust', 'O'), ('van', 'O'), ('Nederland', 'B-LOC')],
            [('Het', 'O'), ('Rijksmuseum', 'B-ORG'), ('bevat', 'O'), ('vele', 'O'), ('meesterwerken', 'O')],
            [('De', 'O'), ('Nederlandse', 'B-LOC'), ('Koninklijke', 'I-LOC'), ('Familie', 'I-LOC'), ('woont', 'O'), ('in', 'O'), ('Den', 'B-LOC'), ('Haag', 'I-LOC')],
            [('Het', 'O'), ('Vondelpark', 'B-LOC'), ('is', 'O'), ('een', 'O'), ('populaire', 'O'), ('bestemming', 'O'), ('in', 'O'), ('Amsterdam', 'B-LOC')]
            ]

In [248]:
# Convertim les dades a BIOES
text_esp = [convert_bio_to_bioes(sent) for sent in text_esp]
text_ned = [convert_bio_to_bioes(sent) for sent in text_ned]

In [249]:
# Amb els models en espanyol i neerlanès entrenats anteriorment
etiquetadas_esp = crf_tagger_esp.tag_sents([word for word, _ in sent] for sent in text_esp)
etiquetadas_ned = crf_tagger_ned.tag_sents([word for word, _ in sent] for sent in text_ned)

In [250]:
real_entities_esp = extract_real_entities(text_esp)
predicted_entities_esp = extract_real_entities(etiquetadas_esp)

In [251]:
real_entities_ned = extract_real_entities(text_ned)
predicted_entities_ned = extract_real_entities(etiquetadas_ned)

In [252]:
precision_esp, recall_esp, f1_score_esp = calculate_metrics(set(predicted_entities_esp), set(real_entities_esp))
print("Resultats obtinguts en espanyol:")
print("Precisió:", precision_esp)
print("Recall:", recall_esp)
print("F1-score:", f1_score_esp)


precision_ned, recall_ned, f1_score_ned = calculate_metrics(set(predicted_entities_ned), set(real_entities_ned))
print("Resultats obtinguts en neerlandès:")
print("Precision:", precision_ned)
print("Recall:", recall_ned)
print("F1-score:", f1_score_ned)

Resultats obtinguts en espanyol:
Precisió: 0.5945945945945946
Recall: 0.5641025641025641
F1-score: 0.5789473684210528
Resultats obtinguts en neerlandès:
Precision: 0.65625
Recall: 0.5833333333333334
F1-score: 0.6176470588235293


# Opcional

Per realitzar aquest apartat utilitzarem funcions definides anteriorment, aquestes són: extract_real_entities per tal d'extreure les entitats i poder avaluar correctament el model, calculate_metrics per calcular l'accuracy, la precisió i el F1-score, les diferents versions de get_features per fer experiments i trobar les característiques que funcionen millor pel model i les funcions per canviar la codificació de BIO a IO i BIOES.

  El codi següent és el del model guanyador, és a dir, tal i com hem comentat en l'informe, hem provat les diferents codificacions i les diferents característiques i hem trobat el que millor funciona que és: BIOES, get_features1.

Per tal de poder llegir les dades definim la funció read_data, que donat un arxiu de text que contè etiquetes d'entitat, retorna una llista d'oracions, on cada oració és una llista de paraules amb les seves etiqeutes d'entitat corresponants.

  Per fer-ho hem tingut en conte l'estructura inicial dels arxius de dades. En aquests fitxers cada columna representa un tipus d'entitat: Adverse Drug Reaction (ADR), Disease (Di), Drug (Dr), Symptom (S), Finding (F). I en cada fila trobem la parula seguida d'identificadors per poder extreure el tipus d'entitat.

In [89]:
def read_data(file_path):
    sentences = []
    sentence = []

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            line = line.strip().split()
            if line:
                word = line[0]
                entity_type = 'O'
                for i in range(1, len(line)):
                    if line[i] != 'O':
                        entity_tag = line[i][0]  # Mantenim només l'etiqueta de l'entitat (B, I)
                        entity_type = ['ADR', 'Di', 'Dr', 'S', 'F'][i - 1]
                        entity_type = entity_tag + '-' + entity_type  
                        break

                sentence.append((word, entity_type))
            else:
                if sentence:
                    sentences.append(sentence)
                    sentence = []
    return sentences


Agafem les dades de train i de test i utilitzem la funció read_data per tal de tenir les dades de la forma que ens interessa pel CRFTagger (paraula, tag)

In [165]:
train_file = "train.conll"
test_file = "test.conll"

In [166]:
train_data = read_data(train_file)
test_data = read_data(test_file)

In [60]:
train_data #per comprovar que ho fagi correctament

[[('LIPITOR.408', 'O'),
  ('pain', 'B-ADR'),
  ('in', 'I-ADR'),
  ('my', 'I-ADR'),
  ('left', 'I-ADR'),
  ('leg', 'I-ADR'),
  ('and', 'O'),
  ('most', 'O'),
  ('of', 'O'),
  ('my', 'O'),
  ('joints', 'I-ADR'),
  ('.', 'O')],
 [('LIPITOR.265', 'O'),
  ('Elevated', 'B-ADR'),
  ('CPK', 'I-ADR'),
  ('levels', 'I-ADR'),
  (',', 'O'),
  ('muscle', 'B-ADR'),
  ('problems', 'I-ADR'),
  (',', 'O'),
  ('felt', 'O'),
  ('bad', 'O'),
  ('.', 'O')],
 [('I', 'O'),
  ('landed', 'O'),
  ('up', 'O'),
  ('having', 'O'),
  ('to', 'O'),
  ('have', 'O'),
  ('a', 'O'),
  ('muscle', 'O'),
  ('biopsy', 'O'),
  ('to', 'O'),
  ('the', 'O'),
  ('right', 'O'),
  ('leg', 'O'),
  ('which', 'O'),
  ('showed', 'O'),
  ('no', 'O'),
  ('muscle', 'O'),
  ('damage', 'O'),
  (',', 'O'),
  ('but', 'O'),
  ('elevated', 'B-ADR'),
  ('CPK', 'I-ADR'),
  ('levels', 'I-ADR'),
  ('still', 'O'),
  ('were', 'O'),
  ('present', 'O'),
  ('.', 'O')],
 [('After', 'O'),
  ('stopping', 'O'),
  ('this', 'O'),
  ('drug', 'O'),
  (',', 'O')

Convertim les dades a BIOES amb la funció definida anteriorment (convert_bio_to_bioes)

In [167]:
# Convertim les dades a BIOES
train_data = [convert_bio_to_bioes(sent) for sent in train_data]
test_data = [convert_bio_to_bioes(sent) for sent in test_data]

In [146]:
train_data

[[('LIPITOR.408', 'O'),
  ('pain', 'B-ADR'),
  ('in', 'I-ADR'),
  ('my', 'I-ADR'),
  ('left', 'I-ADR'),
  ('leg', 'E-ADR'),
  ('and', 'O'),
  ('most', 'O'),
  ('of', 'O'),
  ('my', 'O'),
  ('joints', 'E-ADR'),
  ('.', 'O')],
 [('LIPITOR.265', 'O'),
  ('Elevated', 'B-ADR'),
  ('CPK', 'I-ADR'),
  ('levels', 'E-ADR'),
  (',', 'O'),
  ('muscle', 'B-ADR'),
  ('problems', 'E-ADR'),
  (',', 'O'),
  ('felt', 'O'),
  ('bad', 'O'),
  ('.', 'O')],
 [('I', 'O'),
  ('landed', 'O'),
  ('up', 'O'),
  ('having', 'O'),
  ('to', 'O'),
  ('have', 'O'),
  ('a', 'O'),
  ('muscle', 'O'),
  ('biopsy', 'O'),
  ('to', 'O'),
  ('the', 'O'),
  ('right', 'O'),
  ('leg', 'O'),
  ('which', 'O'),
  ('showed', 'O'),
  ('no', 'O'),
  ('muscle', 'O'),
  ('damage', 'O'),
  (',', 'O'),
  ('but', 'O'),
  ('elevated', 'B-ADR'),
  ('CPK', 'I-ADR'),
  ('levels', 'E-ADR'),
  ('still', 'O'),
  ('were', 'O'),
  ('present', 'O'),
  ('.', 'O')],
 [('After', 'O'),
  ('stopping', 'O'),
  ('this', 'O'),
  ('drug', 'O'),
  (',', 'O')

La següent cel·la ha sigut utilitzada per realitzar els diferents experiments i convertir les dades a IO, amb el model que millor funciona no s'ha d'executar.

In [136]:
#convertim a IO
train_data = [[(word, 'I-' + bio[2:]) if bio.startswith('B-') else (word, bio) for word, bio in sent] for sent in train_data]
test_data = [[(word, 'I-' + bio[2:]) if bio.startswith('B-') else (word, bio) for word, bio in sent] for sent in test_data]

train_data # comprovem que s'hagi fet el canvi correctament

[[('LIPITOR.408', 'O'),
  ('pain', 'I-ADR'),
  ('in', 'I-ADR'),
  ('my', 'I-ADR'),
  ('left', 'I-ADR'),
  ('leg', 'I-ADR'),
  ('and', 'O'),
  ('most', 'O'),
  ('of', 'O'),
  ('my', 'O'),
  ('joints', 'I-ADR'),
  ('.', 'O')],
 [('LIPITOR.265', 'O'),
  ('Elevated', 'I-ADR'),
  ('CPK', 'I-ADR'),
  ('levels', 'I-ADR'),
  (',', 'O'),
  ('muscle', 'I-ADR'),
  ('problems', 'I-ADR'),
  (',', 'O'),
  ('felt', 'O'),
  ('bad', 'O'),
  ('.', 'O')],
 [('I', 'O'),
  ('landed', 'O'),
  ('up', 'O'),
  ('having', 'O'),
  ('to', 'O'),
  ('have', 'O'),
  ('a', 'O'),
  ('muscle', 'O'),
  ('biopsy', 'O'),
  ('to', 'O'),
  ('the', 'O'),
  ('right', 'O'),
  ('leg', 'O'),
  ('which', 'O'),
  ('showed', 'O'),
  ('no', 'O'),
  ('muscle', 'O'),
  ('damage', 'O'),
  (',', 'O'),
  ('but', 'O'),
  ('elevated', 'I-ADR'),
  ('CPK', 'I-ADR'),
  ('levels', 'I-ADR'),
  ('still', 'O'),
  ('were', 'O'),
  ('present', 'O'),
  ('.', 'O')],
 [('After', 'O'),
  ('stopping', 'O'),
  ('this', 'O'),
  ('drug', 'O'),
  (',', 'O')

Entrenem el tagger amb les dades train i predim les dades de test, despres utilitzem les funcions definides anteriorment per avaluar el model

In [168]:
crf_tagger = CRFTagger(feature_func=get_features1) #canviar per get_features1, get_features2, get_features3 o res depenent de quin volem provar 
crf_tagger.train(train_data, 'model.crf.tagger')

In [169]:
etiquetadas_test = crf_tagger.tag_sents([word for word, _ in sent] for sent in test_data)

In [124]:
etiquetadas_test

[[('CATAFLAM.2', 'O'), ('Dry', 'I-ADR'), ('mouth', 'I-ADR'), ('.', 'O')],
 [('Go', 'O'), ('buy', 'O'), ('candy', 'O'), ('.', 'O')],
 [('It', 'O'),
  ("'", 'O'),
  ('s', 'O'),
  ('cheaper', 'O'),
  ('and', 'O'),
  ('have', 'O'),
  ('the', 'O'),
  ('same', 'O'),
  ('effect', 'O'),
  ('on', 'O'),
  ('pain', 'I-ADR'),
  ('.', 'O')],
 [('I', 'O'),
  ('take', 'O'),
  ('it', 'O'),
  ('with', 'O'),
  ('2', 'O'),
  ('propain', 'O'),
  ('(', 'O'),
  ('40', 'O'),
  ('mg', 'O'),
  ('each', 'O'),
  (')', 'O'),
  ('at', 'O'),
  ('a', 'O'),
  ('time', 'O'),
  (',', 'O'),
  ('or', 'O'),
  ('2', 'O'),
  ('mypaid', 'O'),
  ('forte', 'O'),
  ('(', 'O'),
  ('Ibuprofen', 'I-Dr'),
  ('400', 'O'),
  ('mg', 'O'),
  ('Paracetamol', 'I-Dr'),
  ('325', 'O'),
  ('mg', 'O'),
  ('each', 'O'),
  (')', 'O'),
  ('(', 'O'),
  ('Don', 'O'),
  ("'", 'O'),
  ('t', 'O'),
  ('do', 'O'),
  ('this', 'O'),
  ('!!!)', 'O'),
  ('and', 'O'),
  ('it', 'O'),
  ('don', 'O'),
  ("'", 'O'),
  ('t', 'O'),
  ('work', 'O'),
  ('for', 'O'

In [170]:
real_entities = extract_real_entities(test_data)
predicted_entities = extract_real_entities(etiquetadas_test)

In [171]:
precision, recall, f1_score = calculate_metrics(set(predicted_entities), set(real_entities))
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1_score)

Precision: 0.6092165898617512
Recall: 0.37072349971957375
F1-score: 0.4609483960948396
